### Step 1: Import Libraries and csv files

In [1]:
# Import the required libraries
import pandas as pd
from pathlib import Path
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn import metrics
from sklearn.metrics import balanced_accuracy_score, confusion_matrix, classification_report
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler, LabelEncoder, MinMaxScaler
from sklearn.linear_model import Lasso, LinearRegression
from sklearn.metrics import mean_squared_error,r2_score, mean_absolute_error
from sklearn.model_selection import GridSearchCV

import warnings
warnings.filterwarnings('ignore')

In [2]:
# Read the CSV file into a Pandas DataFrame
car_prices_df = pd.read_csv(Path("Resources/car_prices.csv"))

# Review the DataFrame
car_prices_df.head()


year   make                model        trim   body transmission  \
0  2015    Kia              Sorento          LX    SUV    automatic   
1  2015    Kia              Sorento          LX    SUV    automatic   
2  2014    BMW             3 Series  328i SULEV  Sedan    automatic   
3  2015  Volvo                  S60          T5  Sedan    automatic   
4  2014    BMW  6 Series Gran Coupe        650i  Sedan    automatic   

                 vin state  condition  odometer  color interior  \
0  5xyktca69fg566472    ca        5.0   16639.0  white    black   
1  5xyktca69fg561319    ca        5.0    9393.0  white    beige   
2  wba3c1c51ek116351    ca       45.0    1331.0   gray    black   
3  yv1612tb4f1310987    ca       41.0   14282.0  white    black   
4  wba6b2c57ed129731    ca       43.0    2641.0   gray    black   

                                   seller      mmr  sellingprice  \
0                 kia motors america  inc  20500.0       21500.0   
1                 kia motors america  inc  20800.0       21500.0   
2  financial services remarketing (lease)  31900.0       30000.0   
3                 volvo na rep/world omni  27500.0       27750.0   
4  financial services remarketing (lease)  66000.0       67000.0   

                                  saledate  
0  Tue Dec 16 2014 12:30:00 GMT-0800 (PST)  
1  Tue Dec 16 2014 12:30:00 GMT-0800 (PST)  
2  Thu Jan 15 2015 04:30:00 GMT-0800 (PST)  
3  Thu Jan 29 2015 04:30:00 GMT-0800 (PST)  
4  Thu Dec 18 2014 12:30:00 GMT-0800 (PST)

In [3]:
# Check for Null Values
car_prices_df.isnull().sum()

year                0
make            10301
model           10399
trim            10651
body            13195
transmission    65352
vin                 4
state               0
condition       11820
odometer           94
color             749
interior          749
seller              0
mmr                38
sellingprice       12
saledate           12
dtype: int64

In [4]:
#Percentage of null values in data
car_prices_df.isnull().mean()*100

year             0.000000
make             1.843292
model            1.860829
trim             1.905922
body             2.361154
transmission    11.694287
vin              0.000716
state            0.000000
condition        2.115107
odometer         0.016821
color            0.134028
interior         0.134028
seller           0.000000
mmr              0.006800
sellingprice     0.002147
saledate         0.002147
dtype: float64

In [6]:
car_prices_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 558837 entries, 0 to 558836
Data columns (total 16 columns):
 #   Column        Non-Null Count   Dtype  
---  ------        --------------   -----  
 0   year          558837 non-null  int64  
 1   make          548536 non-null  object 
 2   model         548438 non-null  object 
 3   trim          548186 non-null  object 
 4   body          545642 non-null  object 
 5   transmission  493485 non-null  object 
 6   vin           558833 non-null  object 
 7   state         558837 non-null  object 
 8   condition     547017 non-null  float64
 9   odometer      558743 non-null  float64
 10  color         558088 non-null  object 
 11  interior      558088 non-null  object 
 12  seller        558837 non-null  object 
 13  mmr           558799 non-null  float64
 14  sellingprice  558825 non-null  float64
 15  saledate      558825 non-null  object 
dtypes: float64(4), int64(1), object(11)
memory usage: 68.2+ MB


In [7]:
#sns.pairplot(car_prices_df, hue="odometer")

In [8]:


#x_vars= ["year", "odometer", "trim", "body", "transmission","state", "condition", "color"]
#y_vars= ["sellingprice"]
g= sns.PairGrid(car_prices_df, hue="make", x_vars=x_vars, y_vars=y_vars)
#g.map_diag(sns.histplot, color=".3")
g.map_offdiag(sns.scatterplot)
g.add_legend()

NameError: name 'x_vars' is not defined

In [ ]:
#sns.catplot(data=car_prices_df, x="year", y="sellingprice", kind="box")

In [9]:
car_prices_df.dropna(subset=['transmission'])
car_prices_df=car_prices_df.dropna()
car_prices_df= car_prices_df.drop(columns=['vin','saledate','seller'], axis=1)
car_prices_df.head(2)

year make    model trim body transmission state  condition  odometer  \
0  2015  Kia  Sorento   LX  SUV    automatic    ca        5.0   16639.0   
1  2015  Kia  Sorento   LX  SUV    automatic    ca        5.0    9393.0   

   color interior      mmr  sellingprice  
0  white    black  20500.0       21500.0  
1  white    beige  20800.0       21500.0

In [10]:
make_pp= car_prices_df.make.value_counts()[:10]
make_pp.index

Index(['Ford', 'Chevrolet', 'Nissan', 'Toyota', 'Dodge', 'Honda', 'Hyundai',
       'BMW', 'Kia', 'Chrysler'],
      dtype='object', name='make')

In [11]:
tencar_df= car_prices_df[car_prices_df['make'].isin(make_pp.index)]

In [12]:
tencar_df.make.value_counts() , tencar_df.shape

(make
 Ford         81013
 Chevrolet    54150
 Nissan       44043
 Toyota       35313
 Dodge        27181
 Honda        24781
 Hyundai      18659
 BMW          17509
 Kia          15828
 Chrysler     15133
 Name: count, dtype: int64,
 (333610, 13))

In [15]:
tencar_df.duplicated().sum()

0

In [16]:
tencar_df = tencar_df[['year','make','model','trim','transmission','state','condition','odometer','color','interior','mmr','sellingprice']]

In [17]:
tencar_df.head(3)

year make     model        trim transmission state  condition  odometer  \
0  2015  Kia   Sorento          LX    automatic    ca        5.0   16639.0   
1  2015  Kia   Sorento          LX    automatic    ca        5.0    9393.0   
2  2014  BMW  3 Series  328i SULEV    automatic    ca       45.0    1331.0   

   color interior      mmr  sellingprice  
0  white    black  20500.0       21500.0  
1  white    beige  20800.0       21500.0  
2   gray    black  31900.0       30000.0

In [33]:
#selling price, odometer plots
odom= (
    tencar_df.groupby(['make','sellingprice']).sum().mean()
    
)
odom.head()

TypeError: Could not convert ['3 Series3 Series7 Series5 Series5 Series5 Series7 Series7 Series3 Series3 Series3 Series7 Series3 Series5 Series5 Series3 Series3 Series7 Series3 Series3 Series3 Series5 Series5 Series3 Series7 Series7 Series5 Series5 Series3 Series7 Series7 Series3 Series7 Series7 Series3 Series3 Series3 Series3 Series7 Series3 Series3 Series3 Series5 Series5 Series3 Series7 Series3 Series3 Series5 Series7 Series3 Series5 Series3 Series5 Series7 Series5 Series5 Series5 Series5 Series5 Series3 Series3 Series3 Series5 Series3 Series7 Series5 Series7 Series3 Series5 SeriesX55 Series5 Series7 Series3 Series5 Series5 Series3 Series5 Series5 Series7 Series5 Series3 Series7 Series7 Series5 Series5 Series3 Series5 Series5 Series7 Series3 Series3 Series3 Series3 Series7 Series3 Series3 Series3 Series7 Series3 Series3 Series3 Series7 Series5 Series5 Series3 Series5 Series7 Series7 Series3 Series5 Series7 Series3 Series3 Series7 Series7 Series3 Series3 Series3 Series3 Series5 Serie

In [30]:
odom.hvplot(
    x="make",
    y=["odometer", "sellingprice"]
)

AttributeError: 'DataFrameGroupBy' object has no attribute 'hvplot'

In [ ]:
cat_encoder = LabelEncoder()

In [ ]:
for i in tencar_df.columns:
    if tencar_df[i].dtype =='object':
        tencar_df[i] = cat_encoder.fit_transform(tencar_df[i])

In [ ]:
tencar_df.head(3)

In [ ]:
make_sales = tencar_df.corr()
sns.heatmap(make_sales, cmap="Blues", annot=True)

In [ ]:
scaler = MinMaxScaler()

In [ ]:
X= tencar_df.iloc[:,:-1]
y= tencar_df.iloc[:,-1]

In [ ]:
y

In [ ]:
for i in X.columns:
    X[i] = scaler.fit_transform(np.array(X[i]).reshape(-1,1))

In [ ]:
X.head(4)

In [ ]:
xtrain,xtest,ytrain,ytest = train_test_split(X,y,test_size=0.2,random_state=1)

In [ ]:
xtrain.shape, ytrain.shape

In [ ]:
lasso_model = Lasso()
lasso_model.fit(xtrain,ytrain)

In [ ]:
pred=lasso_model.predict(xtest)

In [ ]:
msre = round(np.sqrt(mean_squared_error(ytest,pred)),2)
msre

In [ ]:
mean_squared_error(ytest,pred)

In [ ]:
lasso_model.coef_

In [ ]:
lasso_model.intercept_

In [ ]:
r2_score(ytest,pred)

In [ ]:
param = {'alpha' :[1e-15,1e-10,1e-8,1e-3,1e-2,1,5,10,20,30,40,50,100, 1000, 10000]}

In [ ]:
lasso_twocv= GridSearchCV(lasso_model, param, cv=3, n_jobs=1)

In [ ]:
lasso_twocv.fit(xtrain, ytrain)

In [ ]:
pred_two= lasso_twocv.predict(xtest)

In [ ]:
mean_absolute_error(ytest, pred_two)

In [ ]:
mean_squared_error(ytest, pred_two)

In [ ]:
r2_score(ytest, pred_two)

In [ ]:
lasso_twocv.best_estimator_

In [ ]:
lass_two = Lasso(alpha=10000)

In [ ]:
lass_two.fit(xtrain, ytrain)

In [ ]:
lass_two.intercept_

In [ ]:
lass_two.coef_

In [ ]:
coef_dict={}
for coef, feat in zip(lasso_model.coef_,X.columns):
    coef_dict[feat] = coef
coef_dict

In [ ]:
predict_lasso = lass_two.predict(xtest)


In [ ]:
names = tencar_df.drop('sellingprice',axis=1).columns

print(names)

In [ ]:

lasso = Lasso(alpha=100)
lasso_coef = lasso.fit(X, y).coef_

plt.plot(range(len(names)), lasso_coef)
plt.xticks(range(len(names)), names, rotation=90)
plt.ylabel("Coefficients")
plt.show()

### Step 2: Exploratory Data Analysis

In [ ]:
# Separate the data into target and features

# Separate the y variable, the target
y = car_prices_df["sellingprice"]

# Separate the X variable, the features
X = car_prices_df.drop(columns="sellingprice")

In [ ]:
sns.FacetGrid(car_prices_df, col="make", row="mode")
